In [31]:
"""
This is a modified version of code from: 
    1. https://lawlesst.github.io/notebook/sparql-dataframe.html
    2. https://github.com/SuLab/sparql_to_pandas/blob/master/SPARQL_pandas.ipynb
"""

import pandas as pd
import json
from SPARQLWrapper import SPARQLWrapper, JSON

def get_sparql_dataframe(service, query):
    """
    Helper function to convert SPARQL results into a Pandas data frame.
    """
    sparql = SPARQLWrapper(service)
    sparql.setQuery(query)
    sparql.setReturnFormat(JSON)
    result = sparql.query()

    processed_results = json.load(result.response)
    cols = processed_results['head']['vars']

    out = []
    for row in processed_results['results']['bindings']:
        item = []
        for c in cols:
            item.append(row.get(c, {}).get('value'))
        out.append(item)

    return pd.DataFrame(out, columns=cols)

wds = "https://query.wikidata.org/sparql"
rq = """
SELECT ?disease ?diseaseLabel ?en_article 
WHERE {
  SERVICE wikibase:label { bd:serviceParam wikibase:language "en". }
  ?disease wdt:P31 wd:Q12136.
  
      OPTIONAL {
      ?en_article schema:about ?disease .
      ?en_article schema:inLanguage "en" .
      ?en_article schema:isPartOf <https://en.wikipedia.org/> .
    }
}
#order by desc(?disease)
"""

df = get_sparql_dataframe(wds, rq)

##This is a modified version of code from: https://stackoverflow.com/a/48481247/2339926
def make_clickable_wkt_items(val):
    # target _blank to open new window
    return '<a target="_blank" href="{}">{}</a>'.format(val, val[31:])
def make_clickable_en_articles(val):
    # target _blank to open new window
    if not val: 
        return None
    else:
        return '<a target="_blank" href="{}">{}</a>'.format(val, val[30:])

df.style.format({'disease': make_clickable_wkt_items,'en_article': make_clickable_en_articles})
#df.style.format()

In [2]:
#code from: https://www.kaggle.com/rtatman/download-a-csv-file-from-a-kernel
# import the modules we'll need
from IPython.display import HTML
import pandas as pd
import numpy as np
import base64

# function that takes in a dataframe and creates a text link to  
# download it (will only work for files < 2MB or so)
def create_download_link(df, title = "<b>Download CSV file<b>", filename = "data.csv"):  
    csv = df.to_csv()
    b64 = base64.b64encode(csv.encode())
    payload = b64.decode()
    html = '<a download="{filename}" href="data:text/csv;base64,{payload}" target="_blank">{title}</a>'
    html = html.format(payload=payload,title=title,filename=filename)
    return HTML(html)

# create a link to download the dataframe
create_download_link(df)

In [6]:
#This is a modified version of code from: https://gist.github.com/bonzanini/5a4c39e4c02502a8451d
#https://gist.github.com/bonzanini/5a4c39e4c02502a8451d

# you need to install Biopython:
# pip install biopython

# Full discussion:
# https://marcobonzanini.wordpress.com/2015/01/12/searching-pubmed-with-python/

from Bio import Entrez


def search(query):
    Entrez.email = 'arash.joorabchi@ul.ie'
    handle = Entrez.esearch(db='pubmed', 
                            sort='relevance', 
                            retmax='200',
                            retmode='xml', 
                            term=query)
    results = Entrez.read(handle)
    return results

def fetch_details(id_list):
    ids = ','.join(id_list)
    Entrez.email = 'your.email@example.com'
    handle = Entrez.efetch(db='pubmed',
                           retmode='xml',
                           id=ids)
    results = Entrez.read(handle)
    return results


def pubmed_search(disease):
    results = search("("+disease+"""[title/abstract] NOT "withdrawn"[Title]) AND "The Cochrane database of systematic reviews"[Journal]
    """) 
    #pprint.pprint (results)
    return results['IdList']

    
pubmed_search("tetanus")

['30091147', '29851031', '29342498', '27394698', '27378094', '26621223', '26144877', '26086647', '25803792', '25408540', '24226506', '23728678', '23728640', '22513932', '21735423', '21069697', '19588375', '18425960', '16235306', '16034918', '14974046', '12519624', '11406003']

In [4]:
import wikipedia

from fuzzywuzzy import fuzz
from fuzzywuzzy import process
import re


def searh_wp_refs_4title(pubmedArticleTitle,WPpageTitle):  
    #display (wikipedia.WikipediaPage(WPpageTitle).html())
    WPpageHTML= wikipedia.WikipediaPage(WPpageTitle).html()
    ratio = fuzz.ratio(WPpageHTML, pubmedArticleTitle)
    print ("fuzz.ratio:",ratio)

    WPpageHTML=re.sub(r'\W+', '', WPpageHTML.lower())
    pubmedArticleTitle=re.sub(r'\W+', '', pubmedArticleTitle.lower())
    print(pubmedArticleTitle)
    if pubmedArticleTitle in WPpageHTML:
        return True
    else:
        return False
    
#print (searh_wp_refs_4title("interventions to slow progression of myopia in children...","Near-sightedness"))

def searh_wp_refs_4PMID(PMID,en_article_HTML):
    ''' looksup a PMIDs in a WikiPedia page '''  

    #print('searching for PMID: <b>'+PMID+ '</b>')
    if PMID in en_article_HTML:
        #print ('found')
        return True
    else:
        #print ('not found')
        return False
    

en_article_HTML= wikipedia.WikipediaPage('Near-sightedness').html()
print (searh_wp_refs_4PMID("22161388",en_article_HTML))



True


In [39]:
import wikipedia
from tqdm import tnrange, tqdm_notebook
from urllib.parse import unquote
from IPython.display import clear_output

import ipywidgets as widgets
from ipywidgets import HBox, VBox



df['Cochrane reviews']=""
i=0
for index, row in tqdm_notebook(df.iterrows(),desc='processing diseases',total=df['en_article'].count(), unit="disease"):
    if row['en_article'] is not None:
        print()
        print('------------------------------------------------------------')
        print(i,index,row['diseaseLabel'],row['disease'],row['en_article'])

        en_article_Title = row['en_article'][30:]
        en_article_Title= unquote(unquote(en_article_Title))
        #print(en_article_Title)
        
        en_article_HTML= wikipedia.WikipediaPage(en_article_Title).html()

        id_list= pubmed_search(row['diseaseLabel'])
        matches=0
        if  id_list:
            papers = fetch_details(id_list)
            
            #print(json.dumps(papers, indent=5))
 
            row['Cochrane reviews']="""
            <div align="left" style="margin:10px;">
            <ol start="1" style="margin-left:30px">"""
            
            for j, paper in enumerate(papers['PubmedArticle']):
            
                cited=searh_wp_refs_4PMID(paper['MedlineCitation']['PMID'],en_article_HTML)
                color="red"
                confirmation=" 🗷"
                if cited:
                    matches +=1
                    color="green"
                    confirmation=" 🗹"
                
                row['Cochrane reviews']+='<li style="padding:5px;color:'+color+';">'\
                +paper['MedlineCitation']['Article']['ArticleTitle']\
                +' <a target="_blank" href="https://www.ncbi.nlm.nih.gov/pubmed/'\
                +paper['MedlineCitation']['PMID']+'">PMID: '+paper['MedlineCitation']['PMID']+'</a>'\
                +confirmation+"</li>"
                #print("%d) %s" % (j+1, paper['MedlineCitation']['Article']['ArticleTitle']),paper['MedlineCitation']['PMID'],cited)

                
            row['Cochrane reviews']+="</ol></div>"
                
        else:
            print ("No Cochrane reviews found")
            row['Cochrane reviews']= "No Cochrane reviews found"
            
        print('{} of {} Cochrane reviews found (via PubMed) are cited in the Wikipedia article: {}'.format(matches, len(papers['PubmedArticle']), en_article_Title))
        i += 1


        
       


------------------------------------------------------------
0 0 myopia http://www.wikidata.org/entity/Q168403 https://en.wikipedia.org/wiki/Near-sightedness

------------------------------------------------------------
1 1 psychosis http://www.wikidata.org/entity/Q170082 https://en.wikipedia.org/wiki/Psychosis

------------------------------------------------------------
2 2 Lemierre's syndrome http://www.wikidata.org/entity/Q72000 https://en.wikipedia.org/wiki/Lemierre%27s_syndrome
No Cochrane reviews found

------------------------------------------------------------
3 3 marantic endocarditis http://www.wikidata.org/entity/Q73518 https://en.wikipedia.org/wiki/Nonbacterial_thrombotic_endocarditis
No Cochrane reviews found

------------------------------------------------------------
4 4 oromandibular dystonia http://www.wikidata.org/entity/Q73828 https://en.wikipedia.org/wiki/Oromandibular_dystonia
No Cochrane reviews found

----------------------------------------------------------

KeyboardInterrupt: 

In [37]:
        test= widgets.Textarea(
            value='Hello World',
            placeholder='Type something',
            description='String:',
            disabled=False
        )
        test

Textarea(value='Hello World', description='String:', placeholder='Type something')

In [30]:
df.head(30).style.format({'disease': make_clickable_wkt_items,'en_article': make_clickable_en_articles})

In [ ]:
# create a link to download the dataframe
create_download_link(df)

In [ ]:
from wikidata.client import Client
client = Client()  # doctest: +SKIP
entity = client.get('Q1472', load=True)
print (entity)
print (entity.description)

image_prop = client.get('P18')
image = entity[image_prop]
print (image)

print(image.image_resolution)

print(image.image_url)

